In [1]:
import pandas as pd
import numpy as np
# Load the CSV file into a DataFrame
df = pd.read_csv("tracking_week_6.csv")

# Filter the DataFrame based on the conditions
filtered_df = df[(df['gameId'] == 2022101604) & (df['playId'] == 1264)]

# Create a 'unique_key' column by combining 'gameId' and 'playId'
filtered_df['unique_key'] = filtered_df['gameId'].astype(str) + '_' + filtered_df['playId'].astype(str)

# Load the second CSV file into another DataFrame
plays_df = pd.read_csv("plays.csv")

# Create a 'unique_key' column in plays_df as well
plays_df['unique_key'] = plays_df['gameId'].astype(str) + '_' + plays_df['playId'].astype(str)

# Perform a left join on the 'unique_key' column
result_df = pd.merge(filtered_df, plays_df, on='unique_key', how='left')
tackle_data = pd.read_csv("primaryAndSecondary.csv")

# Filter the DataFrame based on the conditions
tackle_data = tackle_data[tackle_data['unique_key'] == "2022101604_1264"]
frames_after_handoff = tackle_data[tackle_data['frameId'] > 20]
# Count occurrences for primary and secondary tacklers
primary_tackler_counts = frames_after_handoff['primaryTackler'].astype(int).value_counts()
secondary_tackler_counts = frames_after_handoff['secondaryTackler'].astype(int).value_counts()

# Find the most common primary and secondary tacklers
most_common_primary_tackler = primary_tackler_counts.idxmax()
most_common_secondary_tackler = secondary_tackler_counts.idxmax()

# If primary and secondary tacklers are the same, find the next most common secondary tackler
if most_common_primary_tackler == most_common_secondary_tackler:
    secondary_tackler_counts[most_common_secondary_tackler] = 0  # Exclude the most common secondary tackler
    most_common_secondary_tackler = secondary_tackler_counts.idxmax()

# Assign the most common primary and secondary tacklers to the entire column
tackle_data['primaryTackler'] = most_common_primary_tackler
tackle_data['secondaryTackler'] = most_common_secondary_tackler
tackle_data['ballCarrier'] = tackle_data['ballCarrier'].astype(int).value_counts().idxmax()
tackle_data = tackle_data[(tackle_data['frameId'] == 10)] 
result_df = pd.merge(result_df, tackle_data, on='unique_key', how='left')

tackle_results = pd.read_csv('tackles.csv')
# Create a 'unique_key' column by combining 'gameId' and 'playId'
tackle_results['unique_key'] = tackle_results['gameId'].astype(str) + '_' + tackle_results['playId'].astype(str)
tackle_results = tackle_results[tackle_results['unique_key'] == "2022101604_1264"]

# Rename the 'nflId' column to 'actualTackler'
tackle_results.rename(columns={'nflId': 'actualTackler'}, inplace=True)
result_df = pd.merge(result_df, tackle_results, on='unique_key', how='left')

# Set the display option to show all columns
pd.set_option('display.max_columns', None)


/var/folders/83/d5k31zq130zfr34q76sh2l200000gn/T/ipykernel_37589/3025917529.py:10: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_df['unique_key'] = filtered_df['gameId'].astype(str) + '_' + filtered_df['playId'].astype(str)


In [2]:
########### Play Animation ##########
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from matplotlib.lines import Line2D
from IPython.display import HTML

tackleProb_df = pd.read_csv("animationEligibles.csv")

# Get the last column name
last_column_name = tackleProb_df.columns[-1]

# Rename the last column to 'factor'
tackleProb_df.rename(columns={last_column_name: 'factor'}, inplace=True)

# Assuming result_df is your DataFrame
result_df['nflId'].fillna(99999, inplace=True)

# Create a figure and axis
fig, ax = plt.subplots(figsize=(10, 6))

# Set up the initial plot
sc = ax.scatter([], [], color='black')

# Customize plot
ax.set_xlabel('X-axis')
ax.set_ylabel('Y-axis')
ax.set_title('Scatter Plot of X and Y for Each nflId')

# Group by 'frameId'
result_df = result_df[result_df['frameId_x'] < 50]
grouped_df = result_df.groupby('frameId_x')
primaryTackler = result_df['primaryTackler'].iloc[0]
secondaryTackler = result_df['secondaryTackler'].iloc[0]
ballCarrier = result_df['ballCarrier'].iloc[0]
actualTackler = result_df['actualTackler'].iloc[0]

# Animation update function
def update(frame):
    ax.clear()
    defFactors = tackleProb_df[tackleProb_df['frameId']==frame]
    # Use get_group to retrieve the group for the specific frame
    group = grouped_df.get_group(frame)
    
    # Iterate over each row in the frame
    for _, row in group.iterrows():
        marker_edgecolor = False
        if frame >20:
            # Set marker color based on conditions
            marker_color = '#F7FF00'  # Default color
            marker_shape = 'o'
            marker_size = 10
            marker_alpha = 0.3
            if row['nflId'] == primaryTackler:
                marker_color = '#25FE1B'
                marker_shape = 'x'
                marker_size = 40
                marker_alpha = 1
            elif row['nflId'] == secondaryTackler:
                marker_color = '#EC12FE'
                marker_shape = 'x'
                marker_size = 40
                marker_alpha = 1
            elif row['nflId'] == ballCarrier:
                marker_color = '#0231F2'
                marker_shape = '*'
                marker_size = 140
                marker_alpha = 1
                marker_edgecolor='white'
            elif row['possessionTeam'] == row['club']:
                marker_color = '#39CCCC'
            elif 'football' in row['club']:
                marker_color = '#CB7E00'
                marker_shape = 'D'
                marker_size = 20
                marker_alpha = 1
            if frame > 40:
                if row['nflId'] == actualTackler:
                    marker_color = '#FF0000'
                    marker_size = 40
        else:
                        # Set marker color based on conditions
            marker_color = '#F7FF00'  # Default color
            marker_shape = 'o'
            marker_size = 20
            marker_alpha = 1
            if row['possessionTeam'] == row['club']:
                marker_color = '#39CCCC'
            elif 'football' in row['club']:
                marker_color = '#CB7E00'
                marker_shape = 'D'
                marker_size = 20
        if marker_edgecolor:  # Check if marker_edgecolor is specified
            ax.scatter(row['x'], row['y'], label=f'nflId: {row["nflId"]}', color=marker_color, marker=marker_shape, s=marker_size, alpha=marker_alpha, edgecolors=marker_edgecolor)
        else:
            ax.scatter(row['x'], row['y'], label=f'nflId: {row["nflId"]}', color=marker_color, marker=marker_shape, s=marker_size, alpha=marker_alpha)

    # Set background color
    ax.set_facecolor('#415973')
    ax.set_xlabel('')
    ax.set_ylabel('')
    ax.set_title('Example Play Results')

    # Set axis limits
    ax.set_xlim(30, 55)
    ax.set_ylim(10, 43.3)
    
    # Add a horizontal line as a separator between legend groups
    ax.axhline(0, color='white', linewidth=2, linestyle='--')
    # Line of Scrimage
    ax.axvline(x=45, color='white', linestyle='--', linewidth=1)
    # Adjust subplot layout to make space for the legends
    plt.subplots_adjust(right=0.75)

    # Create combined legend handles and labels
    legend_elements = [
        Line2D([0], [0], marker='o', color='w', label='BallCarrier', markerfacecolor='#0231F2', markeredgecolor='#415973',  markersize=10),
        Line2D([0], [0], marker='o', color='w', label='Football', markerfacecolor='#CB7E00', markeredgecolor='#415973',  markersize=10),
        Line2D([0], [0], marker='o', color='w', label='Offense', markerfacecolor='#39CCCC', markeredgecolor='#415973',  markersize=10),
        Line2D([0], [0], marker='o', color='w', label='Defense', markerfacecolor='#F7FF00', markeredgecolor='#415973',  markersize=10),
    ]
    legend_elements2 = [
        Line2D([0], [0], marker='o', color='w', label='PrimaryTackler', markerfacecolor='#25FE1B', markeredgecolor='#415973',  markersize=10),
        Line2D([0], [0], marker='o', color='w', label='SecondaryTackler', markerfacecolor='#EC12FE', markeredgecolor='#415973',  markersize=10),
        Line2D([0], [0], marker='o', color='w', label='ActualTackler', markerfacecolor='#FF0000', markeredgecolor='#415973',  markersize=10),
    ]

    # Place combined legend outside the plot area
    ax.legend(handles=legend_elements + [Line2D([0], [0], color='white', linewidth=2, linestyle='--')] + legend_elements2,
              bbox_to_anchor=(1.05, 0.5), loc='center left')

# Create animation
animation = FuncAnimation(fig, update, frames=grouped_df.groups.keys(), interval=300, repeat=False)

# Display the animation inline in the notebook
html = HTML(animation.to_jshtml())
display(html)

# Save the animation as a GIF
animation.save("animated_plot.gif", writer="pillow")
plt.close()


In [3]:
########## MODIFIED FOR HEAT MAP ##################
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from matplotlib.lines import Line2D
from IPython.display import HTML
from matplotlib.colors import Normalize
from matplotlib.legend_handler import HandlerLine2D

# Adding player names for counter
playerNames = pd.read_csv("players.csv", usecols=['nflId', 'displayName'])
result_df = pd.merge(result_df, playerNames, on='nflId', how='left')
tackleProb_df = pd.read_csv("animationEligibles.csv")
last_column_name = tackleProb_df.columns[-1]
tackleProb_df.rename(columns={last_column_name: 'factor'}, inplace=True)
# Replace all values equal to 100 with 25
tackleProb_df.replace(100, 10, inplace=True)

result_df['nflId'].fillna(99999, inplace=True)

fig, ax = plt.subplots(figsize=(10, 6))
sc = ax.scatter([], [], color='black')

ax.set_xlabel('X-axis')
ax.set_ylabel('Y-axis')
ax.set_title('Scatter Plot of X and Y for Each nflId')

result_df = result_df[result_df['frameId_x'] < 50]
grouped_df = result_df.groupby('frameId_x')
primaryTackler = result_df['primaryTackler'].iloc[0]
secondaryTackler = result_df['secondaryTackler'].iloc[0]
ballCarrier = result_df['ballCarrier'].iloc[0]
actualTackler = result_df['actualTackler'].iloc[0]
# Define counterDict at the global scope
counterDict1 = {}
counterDict2 = {}

def update(frame):
    global counterDict1
    global counterDict2
    
    ax.clear()
    defFactors = tackleProb_df[tackleProb_df['frameId']==frame]
    group = grouped_df.get_group(frame)
    
    legend_elements = []
    for _, row in group.iterrows():
        marker_color = 'white'
        marker_shape = 'o'
        marker_size = 20
        marker_alpha = 1
        marker_edgecolor = False
        if frame >= 20:
            marker_alpha = 0.1
        if row['nflId'] == ballCarrier:
            marker_color = '#0231F2'
            marker_shape = '*'
            marker_size = 140
            marker_alpha = 1
            marker_edgecolor='white'
        elif row['possessionTeam'] == row['club']:
            marker_color = 'white'
        elif 'football' in row['club']:
            marker_color = '#CB7E00'
            marker_shape = 'D'
            marker_size = 20
            marker_alpha = 1
        if row['nflId'] in defFactors['index'].values:
            factor_value = defFactors[defFactors['index'] == row['nflId']]['factor'].values[0]
            # Normalize the factor value before applying to the reversed viridis colormap
            norm = Normalize(vmin=defFactors['factor'].min(), vmax=defFactors['factor'].max())
            marker_color = plt.cm.jet_r(norm(factor_value) - 0.1)
            if abs(norm(factor_value) - 1) < 0.9:
                marker_alpha = 0.3
            else:
                marker_alpha = 1
            marker_size = np.clip(abs(norm(factor_value) - 1) * 10 + 10, 10, 20)  # adjusting size based on probability clip at 20
        
        if marker_edgecolor:  # Check if marker_edgecolor is specified
            scatter = ax.scatter(row['x'], row['y'], color=marker_color, marker=marker_shape, s=marker_size, alpha=marker_alpha, edgecolors=marker_edgecolor)
            ax.text(row['x'], row['y'], f'{row["displayName_x"]}', fontsize=8, color='white', ha='left', va='bottom', alpha=marker_alpha)
        else:
            scatter = ax.scatter(row['x'], row['y'], color=marker_color, marker=marker_shape, s=marker_size, alpha=marker_alpha)
            ax.text(row['x'], row['y'], f'{row["displayName_x"]}', fontsize=8, color='white', ha='left', va='bottom', alpha=marker_alpha)
    
        # Adjust the alpha of the displayName based on the alpha of the scatter plot point
        scatter.set_alpha(marker_alpha)
        # Add velocity sticks
        try:
            speed = row['s']
            direction = 90 - row['dir']  # Adjust the direction to align with 0 degrees being straight up
            dx = speed * np.cos(np.radians(direction))
            dy = speed * np.sin(np.radians(direction))
            ax.arrow(row['x'], row['y'], dx, dy, color='#70F5FE', alpha=0.075, width=0.01, head_width=0.03, head_length=0.03)
        except KeyError:
            pass
    if frame >= 20:
        # Get the row with the minimum 'factor' (primary tackler)
        min_factor_row = defFactors.loc[defFactors['factor'].idxmin()]
    
        # Check if the row exists in playerNames DataFrame
        if not min_factor_row.empty and min_factor_row['index'] in playerNames['nflId'].values:  # Use 'index' instead of 'nflId' if that's the correct column name
            tempName1 = playerNames.loc[playerNames['nflId'] == min_factor_row['index'], 'displayName'].values[0]
        else:
            print("Primary tackler row not found in playerNames DataFrame")
        
        defFactors.loc[defFactors['factor'].idxmin()] = 100

        # Get the row with the second minimum 'factor' (secondary tackler)
        second_min_factor_row = defFactors.loc[defFactors['factor'].idxmin()]

        # Check if the row exists in playerNames DataFrame
        if not second_min_factor_row.empty and second_min_factor_row['index'] in playerNames['nflId'].values:  # Use 'index' instead of 'nflId' if that's the correct column name
            tempName2 = playerNames.loc[playerNames['nflId'] == second_min_factor_row['index'], 'displayName'].values[0]
        else:
            print("Secondary tackler row not found in playerNames DataFrame")
    
        # Add counter to the plot
        if tempName1 not in counterDict1:
            counterDict1[tempName1] = 1
        else:
            counterDict1[tempName1] += 1
    
        if tempName2 not in counterDict2:
            counterDict2[tempName2] = 1
        else:
            counterDict2[tempName2] += 1
        # Find the keys with the largest and second-largest values
        sorted_keys1 = sorted(counterDict1, key=counterDict1.get, reverse=True)
        name1 = sorted_keys1[0]
        sorted_keys2 = sorted(counterDict2, key=counterDict2.get, reverse=True)
        name2 = sorted_keys2[0]# if len(sorted_keys2) > 1 else ''  # Handle the case when there's only one key
        value1 = counterDict1[name1]
        value2 = counterDict2.get(name2, 0)  # Use .get() to handle the case when name2 is not present
        if name1 == name2:
            name2 = sorted_keys2[1]
        # Add counter to the plot
        ax.text(0.2, 0.95, f'{name1}: {value1}/{frame-19}', transform=ax.transAxes, fontsize=12, ha='center', va='center', color='white')
        ax.text(0.75, 0.95, f'{name2}: {value2}/{frame-19}', transform=ax.transAxes, fontsize=12, ha='center', va='center', color='white')
    ax.set_facecolor('#415973')
    ax.set_xlabel('')
    ax.set_ylabel('')
    ax.set_title('Example Calculations (w/velocity vectors)')

    ax.set_xlim(30, 55)
    ax.set_ylim(10, 43.3)
    # Line of Scrimage
    ax.axvline(x=45, color='white', linestyle='--', linewidth=0.5, alpha=0.6)
    #ax.axhline(0, color='white', linewidth=2, linestyle='--')
    plt.subplots_adjust(right=0.75)

    legend_elements += [
        Line2D([0], [0], marker='*', color='w', label='BallCarrier', markerfacecolor='#0231F2', markeredgecolor='black', markersize=10),
        Line2D([0], [0], marker='D', color='w', label='Football', markerfacecolor='#CB7E00', markeredgecolor='black', markersize=10),
        Line2D([0], [0], marker='o', color='w', label='Offense', markerfacecolor='#39CCCC', markeredgecolor='black', markersize=10),
    ]
    
    # Place combined legend outside the plot area
    combined_legend = ax.legend(handles=legend_elements,
                                bbox_to_anchor=(1.05, 0.05), loc='center left')
    
    # Create a ScalarMappable for the color map
    cmap_rectangle = plt.cm.ScalarMappable(cmap='jet', norm=Normalize(vmin=0, vmax=1))
    cmap_rectangle.set_array([])
    
    # Add the color bar next to the legend
    cax = fig.add_axes([0.8, 0.25, 0.018, 0.60])  # Adjust the position and size of the color bar axis
    cbar = plt.colorbar(cmap_rectangle, cax=cax)
    original_legend = ax.get_legend()
    font_properties = original_legend.get_texts()[0].get_font_properties()
    cbar.set_label('Tackler Auction (red is more probable)', labelpad=-50)


animation = FuncAnimation(fig, update, frames=grouped_df.groups.keys(), interval=500, repeat=False)

html = HTML(animation.to_jshtml())
display(html)

animation.save("animated_vector_plot.gif", writer="pillow")
plt.close()
